# RSA au quotidien

## HTTPS et TLS

Les connections sécurisées, par exemple à une banque ou à un site de commerce en ligne, utilisent le protocole HTTPS, une version chiffrée du protocole HTTP, qui repose sur le protocole TLS (*Transport Layer Security*), successeur de SSL (*Secure Socket Layer*).

Le pricipe général est d'utiliser la cryptographie asymétrique pour négocier des clefs de session (*TLS handshake*), et la cryptographie symétrique pour chiffrer les données échangées pendant la session. 
 
Le serveur et le client négocient les détails des algorithmes de chiffrement utilisés et les clefs avant de transmettre aucune donnée.

La cryptographie à clef publique permet  aux deux parties de s'authentifier. Ce n'est pas obligatoire, mais dans le cas d'HTTPS, il faut au moins que le serveur soit authentifié.

Chaque message contient un code d'authentification de message (MAC) qui assure l'intégrité des données transmises.


HTTPS peut chiffrer entièrement les données transmise par HTTP, en particulier l'URL demandée, les paramètres des requètes, les en-têtes el les cookies. Toutefois, les adresse IP du client et du serveur ne peuvent évidemment pas être protégées, non plus que le volume des données transférées.

Les connections TLS utilisent des [certificats](https://en.wikipedia.org/wiki/Public_key_certificate) basés sur des [autorités
de certification](https://en.wikipedia.org/wiki/Certificate_authority), et respectant le standard [X.509](https://en.wikipedia.org/wiki/X.509).

Ces certificats sont pré-installés sur les navigateur, de sorte qu'un utilisateur pourra faire confiance à un site sécurisé seulement si :

- Le navigateur implémente correctement le protocole HTTPS et les certificats sont correctement installés
- L'utilisateur fait confiance aux autorités de certification
- Le site consulté produit un certificat valide
- Le certificat identifie correctement le site
- L'utilisateur fait confiance au protocole TLS


Ces conditions ne sont pas toujours réunies, voir par exemple [ici](https://www.theregister.co.uk/2015/06/03/compromised_ssh_keys_used_to_access_uk_govt_spotify_github_repos/) ou [là](https://news.netcraft.com/archives/2016/03/17/95-of-https-servers-vulnerable-to-trivial-mitm-attacks.html) pour quelques exemples édifiants.


### Certificats X.509

Un certificat se compose essentiellement d'une clef publique, signée par un autorité de certification, possédant elle même un certificat autosigné (certificat racine).

On peut voir les certificats de firefox en allant dans préférences/avancé/certificats :

<img src="screen7.png" width="960" height="540" />



On clique sur "exporter", et on obtient (par défaut) un fichier au format pem.

In [1]:
!cat Amazon

On reconnait un encodage en base 64. Comme pour les clefs ssh, on pourrait décoder le base 64 et continuer avec pyasn1.
Pour cela, il faut connaître la structure du certificat, définie dans la [RFC2459](https://tools.ietf.org/html/rfc2459)


La partie authentifiée contient les champs suivants :
<pre>
    Version
    Numéro de série
    Algorithme de signature du certificat
    DN (Distinguished Name) du délivreur (autorité de certification)
    Validité (dates limites)
        Pas avant
        Pas après
    DN de l'objet du certificat
    Informations sur la clé publique
        Algorithme de la clé publique
        Clé publique proprement dite
    Identifiant unique du signataire (optionnel, X.509v2)
    Identifiant unique du détenteur du certificat (optionnel, X.509v2)
    Extensions (optionnel, à partir de X.509v3)
        Liste des extensions
    Signature des informations ci-dessus par l'autorité de certification
 </pre>
Les noms de l'émetteur (également signataire) comme du titulaire sont des noms X.501, que l'on retrouve également dans les annuaires ISO et LDAP. Le contenu ci-dessus est suivi par une répétition de l'algorithme de signature et de la signature proprement dite.

Pour décoder les certificats, il est plus simple d'utiliser openssl :

In [2]:
!openssl x509 -in Amazon -text

Certificate:
    Data:
        Version: 3 (0x2)
        Serial Number:
            06:7f:94:57:85:87:e8:ac:77:de:b2:53:32:5b:bc:99:8b:56:0d
    Signature Algorithm: sha256WithRSAEncryption
        Issuer: C=US, O=Amazon, CN=Amazon Root CA 1
        Validity
            Not Before: Oct 22 00:00:00 2015 GMT
            Not After : Oct 19 00:00:00 2025 GMT
        Subject: C=US, O=Amazon, OU=Server CA 1B, CN=Amazon
        Subject Public Key Info:
            Public Key Algorithm: rsaEncryption
                Public-Key: (2048 bit)
                Modulus:
                    00:c2:4e:16:67:dd:ce:bc:6a:c8:37:5a:ec:3a:30:
                    b0:1d:e6:d1:12:e8:12:28:48:cc:e8:29:c1:b9:6e:
                    53:d5:a3:eb:03:39:1a:cc:77:87:f6:01:b9:d9:70:
                    cc:cf:6b:8d:e3:e3:03:71:86:99:6d:cb:a6:94:2a:
                    4e:13:d6:a7:bd:04:ec:0a:16:3c:0a:eb:39:b1:c4:
                    b5:58:a3:b6:c7:56:25:ec:3e:52:7a:a8:e3:29:16:
                    07:b9:6e:50:cf:fb:5f:31

On voit donc que les serveurs d'Amazon utilisent une clef RSA de 2048 bits, et une signture RSA d'un hachage SHA256.

Il existe un module tiers, [pyopenssl](https://pyopenssl.readthedocs.io/en/latest/) permettant d'utiliser openssl avec Python.

## Les cartes bancaires

Jusqu'à une époque récente, le paiement par cartes bancaires était authentifié à l'aide d'une simple signature RSA.

La mémoire de la carte est divisée en deux zones, une accessible avec n'importe quel lecteur, et une autre (zone secrète) qui n'est accessible qu'au processeur de la carte, et illisible autrement. La zone publique contient une valeur d'authentification, qui est obtenue en chiffrant des données publiques (comme le numéro de la carte et sa date d'expiration) avec une clé RSA secrète. Les terminaux de paiement et les distributeurs de billets connaissent la clé publique, et l'utilisent pour vérifier la valeur d'authentification, qui est précisément une signature numérique RSA, sans hachage vu le petit nombre de données.

Si la signature est correcte, la carte est considérée comme authentique, et le code est demandé au client. Le terminal envoie le code à la carte qui le compare avec celui contenu dans sa zone secrète, et répond « oui » ou »non ». Si la réponse est « oui », le paiement est accepté.

Vous pourrez au prochain TD déchiffrer les données d'une authentique carte bancaire de l'époque, et en observant leur structure,  forger les données d'une fausse carte à l'aide de la clef factorisée.

Les processeurs des cartes a puces interprètent des instructions appelées APDU (Application Protocol Data Unit) composées de deux octets obligatoires CLA (Class) et INS (Instruction) et de paramètres, par exemple une adresse (en quartets) et le nombre d'octets à lire.

Le résultat se compose des données demandées et de deux octets SW1, SW2 indiquant si tout s'est bien passé. 

Sur un système Linux disposant d'un lecteur de cartes à puce,
il faut installer [pcsc-lite](https://pcsclite.alioth.debian.org/) et activer le démon pcscd.
Il est interfacé avec Python (module [pyscard](https://pyscard.sourceforge.io/). On peut aussi utiliser [gscriptor](https://apps.ubuntu.com/cat/applications/precise/pcsc-tools/), un petite interface graphique pour envoyer des instructions à la carte.

Voici les données à exploiter dans le prochain TD. 

<img src="gscript.png" width="960" height="540" />

On peut trouver des explications détaillées dans cette [archive](cb.pdf) d'un site disparu.